In [2]:

import random
from datetime import timedelta  

# storing and anaysis
import numpy as np
import pandas as pd

# visualization
import matplotlib.pyplot as plt
import plotly.express as px
import folium
from folium import Marker,GeoJson,Choropleth, Circle
from folium.plugins import HeatMap, MarkerCluster

import warnings
warnings.filterwarnings('ignore')

In [3]:
details= pd.read_csv('covid_19_clean_complete.csv', parse_dates=['Date'])
details.sample(5)

Province/State Country/Region      Lat      Long       Date  Confirmed  \
25958            NaN          Ghana   7.9465   -1.0232 2020-04-30       2074   
1389             NaN     Costa Rica   9.7489  -83.7534 2020-01-27          0   
42338         Hainan          China  19.1959  109.7453 2020-07-02        171   
22635            NaN     San Marino  43.9424   12.4578 2020-04-17        435   
43197            NaN           Iraq  33.0000   44.0000 2020-07-05      60479   

       Deaths  Recovered  Active             WHO Region  
25958      17        212    1845                 Africa  
1389        0          0       0               Americas  
42338       6        165       0        Western Pacific  
22635      39         57     339                 Europe  
43197    2473      33017   24989  Eastern Mediterranean

In [3]:
details.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 43848 entries, 0 to 43847
Data columns (total 10 columns):
 #   Column          Non-Null Count  Dtype         
---  ------          --------------  -----         
 0   Province/State  13104 non-null  object        
 1   Country/Region  43848 non-null  object        
 2   Lat             43848 non-null  float64       
 3   Long            43848 non-null  float64       
 4   Date            43848 non-null  datetime64[ns]
 5   Confirmed       43848 non-null  int64         
 6   Deaths          43848 non-null  int64         
 7   Recovered       43848 non-null  int64         
 8   Active          43848 non-null  int64         
 9   WHO Region      43848 non-null  object        
dtypes: datetime64[ns](1), float64(2), int64(4), object(3)
memory usage: 3.3+ MB


In [4]:
full_latest = details[details['Date'] == max(details['Date'])].reset_index()

In [5]:
full_latest.head()

index Province/State Country/Region      Lat     Long       Date  \
0  43587            NaN    Afghanistan  33.0000  65.0000 2020-07-07   
1  43588            NaN        Albania  41.1533  20.1683 2020-07-07   
2  43589            NaN        Algeria  28.0339   1.6596 2020-07-07   
3  43590            NaN        Andorra  42.5063   1.5218 2020-07-07   
4  43591            NaN         Angola -11.2027  17.8739 2020-07-07   

   Confirmed  Deaths  Recovered  Active             WHO Region  
0      33384     920      20179   12285  Eastern Mediterranean  
1       3038      81       1744    1213                 Europe  
2      16879     968      12094    3817                 Africa  
3        855      52        800       3                 Europe  
4        386      21        117     248                 Africa

In [6]:
full_latest.tail()

index Province/State         Country/Region        Lat       Long  \
256  43843            NaN  Sao Tome and Principe   0.186360   6.613081   
257  43844            NaN                  Yemen  15.552727  48.516388   
258  43845            NaN                Comoros -11.645500  43.333300   
259  43846            NaN             Tajikistan  38.861034  71.276093   
260  43847            NaN                Lesotho -29.609988  28.233608   

          Date  Confirmed  Deaths  Recovered  Active             WHO Region  
256 2020-07-07        724      13        279     432                 Africa  
257 2020-07-07       1297     348        591     358  Eastern Mediterranean  
258 2020-07-07        311       7        266      38                 Africa  
259 2020-07-07       6315      53       4965    1297                 Europe  
260 2020-07-07         91       0         11      80                 Africa

In [7]:
full_latest_grouped = full_latest.groupby('Country/Region')['Confirmed', 'Deaths', 'Recovered', 'Active','Lat','Long'].sum().reset_index()

In [8]:
full_latest_grouped.head()

Country/Region  Confirmed  Deaths  Recovered  Active      Lat     Long
0    Afghanistan      33384     920      20179   12285  33.0000  65.0000
1        Albania       3038      81       1744    1213  41.1533  20.1683
2        Algeria      16879     968      12094    3817  28.0339   1.6596
3        Andorra        855      52        800       3  42.5063   1.5218
4         Angola        386      21        117     248 -11.2027  17.8739

In [9]:
full_latest_grouped.tail()

Country/Region  Confirmed  Deaths  Recovered  Active        Lat  \
182  West Bank and Gaza       4647      18        494    4135  31.952200   
183      Western Sahara         10       1          8       1  24.215500   
184               Yemen       1297     348        591     358  15.552727   
185              Zambia       1895      42       1348     505 -15.416700   
186            Zimbabwe        787       9        201     577 -20.000000   

          Long  
182  35.233200  
183 -12.885800  
184  48.516388  
185  28.283300  
186  30.000000

In [11]:
fig = px.choropleth(full_latest_grouped, locations="Country/Region", 
                    locationmode='country names', color=(full_latest_grouped["Confirmed"]), 
                    hover_name="Country/Region", hover_data=['Confirmed'],
                    color_continuous_scale="peach", 
                    title='Countries with Confirmed Cases')
fig.update(layout_coloraxis_showscale=True)
fig.show()

In [34]:
formated_gdf = details.groupby(['Date', 'Country/Region'])['Confirmed', 'Deaths'].max()
formated_gdf = formated_gdf.reset_index()
formated_gdf['Date'] = pd.to_datetime(formated_gdf['Date'])
formated_gdf['Date'] = formated_gdf['Date'].dt.strftime('%m/%d/%Y')
formated_gdf['size'] = formated_gdf['Confirmed'].pow(0.3)

In [29]:
formated_gdf.head()

Date Country/Region  Confirmed  Deaths  size
0  01/22/2020    Afghanistan          0       0   0.0
1  01/22/2020        Albania          0       0   0.0
2  01/22/2020        Algeria          0       0   0.0
3  01/22/2020        Andorra          0       0   0.0
4  01/22/2020         Angola          0       0   0.0

In [30]:
formated_gdf.tail()

Date      Country/Region  Confirmed  Deaths       size
31411  07/07/2020  West Bank and Gaza       4647      18  12.593655
31412  07/07/2020      Western Sahara         10       1   1.995262
31413  07/07/2020               Yemen       1297     348   8.587801
31414  07/07/2020              Zambia       1895      42   9.622386
31415  07/07/2020            Zimbabwe        787       9   7.392518

In [31]:


fig = px.scatter_geo(formated_gdf, locations="Country/Region", locationmode='country names', 
                     color="Confirmed", size='size', hover_name="Country/Region", 
                      animation_frame="Date", 
                     title='Spread over time')
fig.update(layout_coloraxis_showscale=False)
fig.show()

In [6]:
m = folium.Map(location=[54,15], tiles='cartodbpositron', zoom_start=2)

# Add points to the map
mc = MarkerCluster()
for idx, row in full_latest_grouped.iterrows():
    mc.add_child(Marker([row['Lat'], row['Long']], popup=row['Deaths']))
m.add_child(mc)

# Display the map
m

In [11]:
m = folium.Map(location=[54,15], tiles='cartodbpositron', zoom_start=2)

# Add points to the map
mc = MarkerCluster().add_to(m)

for idx, row in full_latest_grouped.iterrows():
    folium.Marker([row['Lat'], row['Long']], popup=row['Deaths']).add_to(mc)
 
folium.LayerControl().add_to(m)

# Display the map
m